#Readme

This notebook calculates the load duration curve and heating demands for a simulation of a single building

*Duration:* The duration for which you want to analysis. Can be one of the following: *day/week/month/year*

*result:* Result file name relative to this notebook

In [1]:
duration = 'year'
result = '../../../Results/haarhakker-year-occ4.mat'

## Contents

- [Real time powers](#Powers)
- [Load duration curves](#Load-duration-curves)
- [Energy](#Energy)

In [2]:
import sys
sys.path.append('/home/arnout/Projects/Work/ModelicaRes/')
sys.path.append('/home/arnout/Projects/Work/python-highcharts')
sys.path.append('/home/arnout/Projects/Work/util')

from modelicares import SimRes, SimResList
from charts import plot, plotasync

import util as u
import numpy as np
import datetime

Server running in the folder /home/arnout/Modelica/DeSchipjes/Notebooks/Single building/Load duration curve at 127.0.0.1:46760


In [3]:
duration = u.toseconds(duration, minus=86400)
print duration

31470526


In [4]:
load_names = {
    'hea.Q_flow': 'Total heat flow',
    'buildingTest.heatingSystem.QHeaSys': 'Heating system heat flow'
}

In [5]:
data = SimRes(result)

In [6]:
# Equi-distant time vector
minutes = 15
points = duration / (60*minutes)
t = [60*minutes*i for i in range(24*(60/minutes), points)]

dates = map(datetime.datetime.fromtimestamp, t)   

# Get the loads at times t
loads = []
for name, description in load_names.iteritems():
    v = u.tonp(data[name], t)
    loads.append(u.toseries(name, v))
    
# Get the DHW load
y = np.array(loads[0]['data'])[:,1] - np.array(loads[1]['data'])[:,1]
y[y<0] = 0 
x = map(lambda u: u*1000, t)

loads.append(dict(name='DHW heat flow', data=np.array([x,y]).T))

### Powers
Plot of the real time powers of the building

In [7]:
options = {
    'chart': {
        'zoomType': 'xy'
    },
    'legend': {
        'enabled': True
    }
}

plot(loads, options, stock=True, show='inline', height=550, save='powers.html')

In [8]:
## Load duration curve calculations

# Sort by power
ldcTotal = sorted(loads[0]['data'], lambda x,y: cmp(y[1], x[1]))
ldcHeating   = sorted(loads[1]['data'], lambda x,y: cmp(y[1], x[1]))
ldcDHW = sorted(loads[2]['data'], lambda x,y: cmp(y[1], x[1]))

# Reset time 
ldcTotal   = [[t[i]*1000, x[1]] for i,x in enumerate(ldcTotal)]
ldcHeating = [[t[i]*1000, x[1]] for i,x in enumerate(ldcHeating)]
ldcDHW     = [[t[i]*1000, x[1]] for i,x in enumerate(ldcDHW)]

# Create series array
series = [
    dict(name='Total', data=ldcTotal),
    dict(name='Heating', data=ldcHeating),
    dict(name='DHW', data=ldcDHW)
]

### Load duration curves

In [9]:
plot(series, options, show='inline', stock=True, height=550, save='ldc.html')

In [10]:
# Cumulative energy demand
Etot = u.tokwh(u.tonp(data['ETot'], t))
Ehea = u.tokwh(u.tonp(data['buildingTest.heatingSystem.SpaceQ'], t))

loads.append(u.toseries('Total cumulative Energy', Etot))
loads.append(u.toseries('Heating energy demand', Ehea))

### Energy

In [11]:
series = loads[3:]
plot(series, options, show='inline', stock=True, height=550, save='energy.html')

### Save the data to an excel file

In [13]:
u.toexcel('data.xlsx', data, [
    'hea.Q_flow', 
    'buildingTest.heatingSystem.QHeaSys', 
    'ETot', 
    'buildingTest.heatingSystem.SpaceQ'
])